# Playing with Metop  AVHRR data

### Summary
In this tutorial, we will read Metop AVHRR data and display a few composites, in satellite projection and on a couple of areas, and add coastlines to some images.

##  Finding the files, filtering with time
The data for this tutorial is comprised of a handfull of Metop-B AVHRR/3 granules, that span over a couple of hours time. Since we just want work with a fraction of all that data, one solution is to define a start and end time and filter the files we provide to `Scene`

In [ ]:
from satpy import Scene, find_files_and_readers
from datetime import datetime
import pprint

files = find_files_and_readers(base_dir='/tcenas/scratch/pytroll/ex2',
                               reader='avhrr_l1b_eps',
                               start_time=datetime(2018, 10, 7 ,9, 25),
                               end_time=datetime(2018, 10, 7 , 9, 30))

#files=sorted(files)
scn = Scene(filenames=files)
pprint.pprint(files)

Then we decide on a composite to load and display it on screen

In [ ]:
print(scn.available_composite_names())

In [ ]:
composite = 'overview'
scn.load([composite])
scn.show(composite)


## Resampling and displaying with coastlines
Resampling is done exactly as in the previous tutorial. However this time we will display the data with coastlines on top.

In [ ]:
newscn = scn.resample('euro1')


In [ ]:
newscn.show(composite, overlay={'coast_dir': '/tcenas/scratch/pytroll/shapes/', 'color': (255, 0, 0), 'resolution': 'i'})


For more information on which parameters you can pass for the coastline burning, check the pycoast documentation.

## Dynamic area resampling
For polar data, it can be convenient do resample the data in a given projection, but adapt the area extent to the actual data being resampled. For this, we have at the moment two dynamic areas we can use: `omerc_bb` for the oblique mercator projection and `laea_bb` for the lambert azimuthal equal-area projection. _Note_: `laea_bb` here will not yield a sensible result for the used dataset.

In [ ]:
# Resample and show the image
newscn = scn.resample('omerc_bb')
newscn.show(composite, overlay={'coast_dir': '/tcenas/scratch/pytroll/shapes/', 'color': (255, 0, 0), 'resolution': 'i'})


## Filtering the data by area
When we have many data granules, it can be convenient to load only those covering a given area. We can achieve this by using the parameter filtering during the `Scene` instanciation

In [ ]:
files = find_files_and_readers(base_dir='/tcenas/scratch/pytroll/ex2',
                               reader='avhrr_l1b_eps')
scn = Scene(filenames=files, filter_parameters={'area':'germ'})

In [ ]:
composite = 'natural_color'
scn.load([composite])
newscn = scn.resample('eurol')
newscn.show(composite, overlay={'coast_dir': '/tcenas/scratch/pytroll/shapes/', 'color': (255, 0, 0), 'resolution': 'i'})

## Saving the data
Satpy allows you to save the data in various formats, e.g. GeoTIFF

In [ ]:
newscn.save_dataset(composite,filename='my_fantastic_image.tiff')
#newscn.save_dataset(composite,filename='my_fantastic_image.nc')

### Exercise 2.1
Generate an `ndvi` product using the individual channels and display the result on the `euron1` area. Then save your work as PNG.

NDVI formula: ndvi = (vis08 - vis06) / (vis08 + vis06)